<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><ul class="toc-item"><li><span><a href="#Setup" data-toc-modified-id="Setup-0.1"><span class="toc-item-num">0.1&nbsp;&nbsp;</span>Setup</a></span></li></ul></li><li><span><a href="#Implement-SGVI" data-toc-modified-id="Implement-SGVI-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Implement SGVI</a></span></li><li><span><a href="#Direct-predictive-accuracy-for-SGVI" data-toc-modified-id="Direct-predictive-accuracy-for-SGVI-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Direct predictive accuracy for SGVI</a></span></li></ul></div>

In [1]:
from functools import lru_cache
import os

import numpy as np
import pandas as pd

import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

from tqdm.notebook import tqdm

In this assignment, you will experiment with Bayesian inference and Stochastic Gradient Variational Inference. Specifically, you will implement Bayesian logistic regression with stochastic gradient variational inference.

## Setup

In [2]:
X_train = np.loadtxt('./Data/X_train.csv')
y_train = np.loadtxt('./Data/Y_train.csv')

X_test = np.loadtxt('./Data/X_test.csv')
y_test = np.loadtxt('./Data/Y_test.csv')

print('Shapes:')
print('X_train', X_train.shape)
print('y_train', y_train.shape)
print('X_test', X_test.shape)
print('y_test', y_test.shape)

Shapes:
X_train (100, 5)
y_train (100,)
X_test (1000, 5)
y_test (1000,)


# Implement SGVI

In [3]:
def sigmoid(x):
    return 1 / (1 + np.exp(-x))

In [4]:
def sample_normal(mean = np.zeros(5), covar = .5 * np.identity(5), sample_size=None):
    return np.random.multivariate_normal(mean, covar, size=sample_size)

In [5]:
def elbo_gradient(w, x, y):
    N, D = x.shape
    
    # Sample from variational distribution
    z = sample_normal(mean = w)

    y = y.reshape((-1, 1))
    z = z.reshape((-1, 1))
    
    t = (x @ z)
    assert t.shape == y.shape
    
    t = -y * t
    t = sigmoid(t)
    t = t * y * x

    grad = -z.ravel() + t.sum(axis=0)

    assert grad.shape == (D,)

    return grad

# Sanity
elbo_gradient(w=np.zeros(5), x=X_train, y=y_train)

array([-4.13443405, -0.4590359 , -6.58061353,  2.98908026, -6.85181978])

In [6]:
def sgvi(data, labels, t_max = 10000, step_size = .005, eval_every=None):
    '''
    Run Stochastic Gradient Variational Inference
    '''

    w = np.zeros(5)
    w_hist = []
    err_rates = []

    for t in range(t_max):
        w_grad = elbo_gradient(w, data, labels)
        w += step_size * w_grad
        
        if eval_every and t % eval_every == 0:
            err_rates.append(evaluate(X_test, y_test, w, repeat=100))

        # Track w across all dimensions
        w_hist.append(w.copy())

    # History shape: dim x iterations
    w_hist = np.array(w_hist).T
    err_rates = np.array(err_rates)

    # Return final w and history
    return w, w_hist, err_rates

final_w, w_hist, err_rates = sgvi(X_train, y_train)

In [7]:
fig = go.Figure()

for i in range(len(w_hist)):
    iterations = list(range(len(w_hist[i])))
    fig.add_trace(go.Scatter(x=iterations, y=w_hist[i], name=f'Dim {i}', mode='lines'))

fig.update_layout(xaxis_title='Iterations')
fig.show()

# Direct predictive accuracy for SGVI

In [8]:
def evaluate(data, labels, w, repeat=1):
    num_samples = len(data)

    # Get a samples from the posterior
    z = sample_normal(mean=w, sample_size=repeat)

    preds = sigmoid(data @ z.T)

    # Average over all samples to get final probability
    preds = preds.mean(axis=1)

    # Threshold the values
    preds = np.where(preds >= .5, 1., -1.).ravel()
    labels = labels.ravel()

    err_rate = (preds != labels).sum() / num_samples

    return err_rate

In [9]:
num_iterations = [10, 100, 1000, 10000]
repetitions = 5
err_rates = np.zeros((len(num_iterations), repetitions))

for it, num_it in tqdm(enumerate(num_iterations), total=len(num_iterations), desc='Iterations'):
    for i in range(repetitions):
        w, w_hist, err_rate = sgvi(X_train, y_train, t_max=num_it)
        err_rates[it, i] = evaluate(X_test, y_test, w, repeat=1000)

err_rates

array([[0.149, 0.205, 0.155, 0.153, 0.159],
       [0.147, 0.144, 0.146, 0.15 , 0.144],
       [0.143, 0.147, 0.145, 0.139, 0.14 ],
       [0.145, 0.144, 0.145, 0.144, 0.143]])

In [10]:
step_sizes = [.0005, .001, .005, .01, .1, 1]

num_iterations = 1000
eval_every=10

w2_value = np.zeros((len(step_sizes), num_iterations))
err_rates = np.zeros((len(step_sizes), num_iterations // eval_every))

for s, step_size in tqdm(enumerate(step_sizes), total=len(step_sizes)):
    w, w_hist, err_rate = sgvi(X_train, y_train, t_max=num_iterations, step_size=step_size, eval_every=eval_every)
    w2_value[s] = w_hist[2]
    err_rates[s] = err_rate

In [11]:
fig = go.Figure()
iterations = np.arange(num_iterations)
eval_steps = np.arange(num_iterations // eval_every) * eval_every

for s, sz in enumerate(step_sizes):
    
    fig.add_trace(go.Scatter(x=eval_steps, y=err_rates[s], name=f'Err rate {sz}', mode='lines'))

fig.update_layout(xaxis_title='Eval Steps', yaxis_title='Err rate')
fig.show()

In [12]:
iterations = [100, 1000, 10000]
eval_every=10

err_rates = []

for s, it in tqdm(enumerate(iterations), total=len(iterations)):
    w, w_hist, err_rate = sgvi(X_train, y_train, t_max=it, step_size=step_size, eval_every=eval_every)
    err_rates.append(err_rate)